In [17]:
import numpy as np
import random
import pandas as pd
from scipy.stats import truncnorm
from bokeh.plotting import figure, show, output_notebook
from bokeh.layouts import column
from bokeh.models import ColumnDataSource, BoxAnnotation, HoverTool
from bokeh.palettes import RdYlGn
import warnings

# Отключение предупреждений
warnings.filterwarnings("ignore")

# Для отображения графиков в Jupyter Notebook
output_notebook()

# Функция для генерации усечённого нормального распределения
def truncated_normal(mean, std, lower, upper, n):
    a, b = (lower - mean) / std, (upper - mean) / std
    return truncnorm(a, b, loc=mean, scale=std).rvs(n)

# Обновлённые спецификации параметров с учётом физики и дополнительных полей
parameter_specs = {
    "vibration_axis": {
        "dist": lambda n: truncated_normal(0.4, 0.05, 0.2, 0.5, n),
        "mean": 0.4,
        "std": 0.05,
        "normal_low": 0.2,
        "normal_high": 0.5,
        "crit_low": 0.1,
        "crit_high": 0.6,
        "failure_behavior": "increase",  # Повышение значения при неисправности
        "default_trend": "exponential",
        "failure_rate": 2,  # Вероятность отказа
        "post_failure_behavior": "hold"  # Поведение после отказа
    },
    "active_power": {
        "dist": lambda n: truncated_normal(90, 5, 70, 110, n),
        "mean": 90,
        "std": 5,
        "normal_low": 70,
        "normal_high": 110,
        "crit_low": 35,
        "crit_high": 145,
        "failure_behavior": "increase",
        "default_trend": "linear",
        "failure_rate": 2,
        "post_failure_behavior": "zero"
    },
    "current_frequency": {
        "dist": lambda n: truncated_normal(50, 0.5, 48, 52, n),
        "mean": 50,
        "std": 0.5,
        "normal_low": 48,
        "normal_high": 52,
        "crit_low": 40,
        "crit_high": 55,
        "failure_behavior": "decrease",
        "default_trend": "constant",
        "failure_rate": 1,
        "post_failure_behavior": "zero"
    },
    "control_station_power": {
        "dist": lambda n: truncated_normal(100, 10, 80, 120, n),
        "mean": 100,
        "std": 10,
        "normal_low": 80,
        "normal_high": 120,
        "crit_low": 30,
        "crit_high": 170,
        "failure_behavior": "increase",
        "default_trend": "linear",
        "failure_rate": 1,
        "post_failure_behavior": "zero"
    },
    "operating_current": {
        "dist": lambda n: truncated_normal(25, 2, 20, 30, n),
        "mean": 25,
        "std": 2,
        "normal_low": 20,
        "normal_high": 30,
        "crit_low": 5,
        "crit_high": 55,
        "failure_behavior": "increase",
        "default_trend": "linear",
        "failure_rate": 2,
        "post_failure_behavior": "zero"
    },
    "motor_temperature": {
        "dist": lambda n: truncated_normal(60, 5, 50, 70, n),
        "mean": 60,
        "std": 5,
        "normal_low": 50,
        "normal_high": 70,
        "crit_low": 20,
        "crit_high": 95,
        "failure_behavior": "increase",
        "default_trend": "linear",
        "failure_rate": 2,
        "post_failure_behavior": "decrease"
    },
    "motor_load": {
        "dist": lambda n: truncated_normal(75, 10, 60, 90, n),
        "mean": 75,
        "std": 10,
        "normal_low": 60,
        "normal_high": 90,
        "crit_low": 25,
        "crit_high": 125,
        "failure_behavior": "increase",
        "default_trend": "linear",
        "failure_rate": 1,
        "post_failure_behavior": "zero"
    },
    "input_pressure": {
        "dist": lambda n: truncated_normal(15, 2, 12, 18, n),
        "mean": 15,
        "std": 2,
        "normal_low": 12,
        "normal_high": 18,
        "crit_low": 2.5,
        "crit_high": 27.5,
        "failure_behavior": "decrease",
        "default_trend": "linear_decrease",
        "failure_rate": 1,
        "post_failure_behavior": "decrease"
    },
    "output_pressure": {
        "dist": lambda n: truncated_normal(25, 2, 22, 28, n),
        "mean": 25,
        "std": 2,
        "normal_low": 22,
        "normal_high": 28,
        "crit_low": 10,
        "crit_high": 40,
        "failure_behavior": "decrease",
        "default_trend": "linear_decrease",
        "failure_rate": 1,
        "post_failure_behavior": "decrease"
    },
    "flow_rate": {
        "dist": lambda n: truncated_normal(50, 5, 40, 60, n),
        "mean": 50,
        "std": 5,
        "normal_low": 40,
        "normal_high": 60,
        "crit_low": 20,
        "crit_high": 80,
        "failure_behavior": "decrease",
        "default_trend": "exponential_decrease",
        "failure_rate": 2,
        "post_failure_behavior": "zero"
    },
    "resistance": {
        "dist": lambda n: truncated_normal(18, 1, 16, 20, n),
        "mean": 18,
        "std": 1,
        "normal_low": 16,
        "normal_high": 20,
        "crit_low": 10,
        "crit_high": 24,
        "failure_behavior": "decrease",
        "default_trend": "exponential_decrease",
        "failure_rate": 1,
        "post_failure_behavior": "increase"
    },
    "bearing_temperature": {  # Добавлен новый параметр
        "dist": lambda n: truncated_normal(40, 3, 35, 45, n),
        "mean": 40,
        "std": 3,
        "normal_low": 35,
        "normal_high": 45,
        "crit_low": 25,
        "crit_high": 55,
        "failure_behavior": "increase",
        "default_trend": "linear",
        "failure_rate": 2,
        "post_failure_behavior": "zero"
    },
    "shaft_speed": {  # Добавлен новый параметр
        "dist": lambda n: truncated_normal(1500, 100, 1400, 1600, n),
        "mean": 1500,
        "std": 100,
        "normal_low": 1400,
        "normal_high": 1600,
        "crit_low": 1200,
        "crit_high": 1800,
        "failure_behavior": "increase",
        "default_trend": "linear",
        "failure_rate": 2,
        "post_failure_behavior": "zero"
    }
}

# Добавление зависимостей между параметрами
def correlate_parameters(data_df, correlations):
    for (param1, param2), coeff in correlations.items():
        data_df[param2] += data_df[param1] * coeff
    return data_df

# Функция генерации данных
def generate_data(number_of_intervals, chosen_parameters, parameter_specs):
    total_iterations = 1000  # Общее количество точек данных
    pump_failed = False  # Флаг отказа насоса
    data_df = pd.DataFrame(index=range(total_iterations))

    # Генерация временных меток с шагом в 1 час
    data_df['ds'] = pd.date_range(start='2025-01-01', periods=total_iterations, freq='1H')  # Исправлено 'H' на '1H'

    # Генерация начальных данных
    for param in parameter_specs:
        data_df[param] = parameter_specs[param]["dist"](total_iterations)

    # Корреляции между параметрами
    correlations = {
        ("vibration_axis", "motor_temperature"): 0.2,
        ("motor_load", "operating_current"): 0.2,
        ("operating_current", "active_power"): 0.3,
        ("motor_temperature", "motor_load"): 0.2,
        ("input_pressure", "output_pressure"): 0.3,
        ("flow_rate", "input_pressure"): 0.2,
        ("resistance", "motor_temperature"): -0.2,
        ("bearing_temperature", "motor_temperature"): 0.1,
        ("shaft_speed", "motor_load"): 0.1
    }
    data_df = correlate_parameters(data_df, correlations)

    # Ограничение значений параметров в пределах нормальной зоны
    for param in parameter_specs:
        normal_low = parameter_specs[param]["normal_low"]
        normal_high = parameter_specs[param]["normal_high"]
        data_df[param] = data_df[param].clip(lower=normal_low, upper=normal_high)

    # Метка состояния насоса:
    # 0 - нормальная работа
    # 1 - негативное влияние параметра
    # 2 - отказ насоса
    data_df['label'] = 0

    # Список для хранения интервалов аномалий
    anomaly_intervals = []

    # Применение трендов и аномалий
    for _ in range(number_of_intervals):
        if pump_failed:
            break  # Останавливаем генерацию аномалий после отказа насоса

        # Выбор параметра с учётом вероятности отказа
        param = random.choices(
            chosen_parameters,
            weights=[parameter_specs[p].get("failure_rate", 1) for p in chosen_parameters],
            k=1
        )[0]
        trend_type = parameter_specs[param]["default_trend"]
        trend_direction = 1 if parameter_specs[param]["failure_behavior"] == "increase" else -1
        n = random.randrange(50, 101)  # Длина интервала (уменьшено для более частых аномалий)
        start_index = random.randrange(0, total_iterations - n)

        # Уровень воздействия (1 - негативное влияние, 2 - отказ)
        influence_level = random.choices([1, 2], weights=[5, 1])[0]  # Увеличена вероятность негативного влияния

        # Применение тренда
        indices = np.arange(n)
        t = indices / n
        std = parameter_specs[param]["std"]
        if trend_type == "linear":
            trend = trend_direction * t * std * 3
        elif trend_type == "linear_decrease":
            trend = trend_direction * t * std * 3
        elif trend_type == "exponential":
            trend = trend_direction * (np.exp(t * 2) - 1) * std
        elif trend_type == "exponential_decrease":
            trend = trend_direction * (1 - np.exp(-t * 2)) * std
        elif trend_type == "sinusoidal":
            trend = trend_direction * np.sin(2 * np.pi * t) * std
        elif trend_type == "constant":
            trend = np.zeros(n)

        # Применение тренда к данным
        failure_occurred = False
        for k in range(n):
            idx = start_index + k
            if idx >= total_iterations:
                break
            base_value = data_df.loc[idx, param]
            new_value = base_value + trend[k]

            # Проверка на критические значения
            if (new_value >= parameter_specs[param]["crit_high"] and trend_direction > 0) or \
               (new_value <= parameter_specs[param]["crit_low"] and trend_direction < 0):
                # Отказ происходит
                data_df.loc[idx, param] = parameter_specs[param]["crit_high"] if trend_direction > 0 else parameter_specs[param]["crit_low"]
                data_df.loc[idx, 'label'] = max(data_df.loc[idx, 'label'], 2)  # Устанавливаем метку отказа
                # Регистрация интервала аномалии
                anomaly_intervals.append((start_index, idx, param, 2))
                failure_occurred = True
                pump_failed = True  # Насос вышел из строя
                # Настройка параметров после отказа
                for p in parameter_specs:
                    post_behavior = parameter_specs[p].get("post_failure_behavior", "hold")
                    if post_behavior == "zero":
                        data_df.loc[idx+1:, p] = 0
                    elif post_behavior == "hold":
                        data_df.loc[idx+1:, p] = data_df.loc[idx, p]
                    elif post_behavior == "increase":
                        data_df.loc[idx+1:, p] = parameter_specs[p]["crit_high"]
                    elif post_behavior == "decrease":
                        data_df.loc[idx+1:, p] = parameter_specs[p]["crit_low"]
                data_df.loc[idx+1:, 'label'] = 2
                break
            else:
                # Обновление значения параметра
                data_df.loc[idx, param] = new_value
                data_df.loc[idx, 'label'] = max(data_df.loc[idx, 'label'], influence_level)

        if not failure_occurred:
            # Если отказ не произошёл, регистрируем интервал аномалии
            anomaly_intervals.append((start_index, start_index + n - 1, param, influence_level))

    # Ограничение значений параметров критическими значениями (повторно для корректности)
    for param in parameter_specs:
        crit_low = parameter_specs[param]["crit_low"]
        crit_high = parameter_specs[param]["crit_high"]
        data_df[param] = data_df[param].clip(lower=crit_low, upper=crit_high)

    return data_df, anomaly_intervals

# Функция визуализации данных с использованием Bokeh
def plot_parameters(data_df, anomaly_intervals):
    params = list(parameter_specs.keys())
    plots = []
    # Создание отображения названий параметров на русском
    russian_labels = {
        "vibration_axis": "Вибрация по оси",
        "active_power": "Активная мощность",
        "current_frequency": "Частота тока",
        "control_station_power": "Мощность контрольной станции",
        "operating_current": "Рабочий ток",
        "motor_temperature": "Температура двигателя",
        "motor_load": "Нагрузка на двигатель",
        "input_pressure": "Давление на входе",
        "output_pressure": "Давление на выходе",
        "flow_rate": "Расход жидкости",
        "resistance": "Сопротивление",
        "bearing_temperature": "Температура подшипников",
        "shaft_speed": "Скорость вращения вала"
    }
    
    for param in params:
        # Автомасштабирование оси Y
        y_min = data_df[param].min() * 0.9
        y_max = data_df[param].max() * 1.1

        p = figure(title=russian_labels[param], width=900, height=250, x_axis_label='Время', y_axis_label=param,
                   tools="pan,wheel_zoom,box_zoom,reset,save", y_range=(y_min, y_max), x_axis_type='datetime')

        source = ColumnDataSource(data=dict(
            x=data_df['ds'],
            y=data_df[param],
            label=data_df['label'],
            time=data_df['ds']
        ))

        # Добавление цветовых зон
        normal_low = parameter_specs[param]["normal_low"]
        normal_high = parameter_specs[param]["normal_high"]
        crit_low = parameter_specs[param]["crit_low"]
        crit_high = parameter_specs[param]["crit_high"]

        # Закрашивание зон с использованием BoxAnnotation
        green_box = BoxAnnotation(top=normal_high, bottom=normal_low, fill_color='green', fill_alpha=0.1)
        yellow_box_top = BoxAnnotation(top=crit_high, bottom=normal_high, fill_color='yellow', fill_alpha=0.1)
        yellow_box_bottom = BoxAnnotation(top=normal_low, bottom=crit_low, fill_color='yellow', fill_alpha=0.1)
        red_box_top = BoxAnnotation(top=y_max, bottom=crit_high, fill_color='red', fill_alpha=0.1)
        red_box_bottom = BoxAnnotation(top=crit_low, bottom=y_min, fill_color='red', fill_alpha=0.1)

        # Добавляем BoxAnnotation в нужном порядке
        p.add_layout(green_box)
        p.add_layout(yellow_box_top)
        p.add_layout(yellow_box_bottom)
        p.add_layout(red_box_top)
        p.add_layout(red_box_bottom)

        # Добавление линии графика
        p.line('x', 'y', source=source, color='black', alpha=0.7, legend_label='Значение')

        # Создание цветов для каждой точки в зависимости от зоны
        colors = []
        for value in data_df[param]:
            if normal_low <= value <= normal_high:
                colors.append('green')  # Нормальная зона
            elif (crit_low <= value < normal_low) or (normal_high < value <= crit_high):
                colors.append('yellow')  # Предкритическая зона
            else:
                colors.append('red')  # Критическая зона
        source.data['color'] = colors

        # Добавление точек на график с лёгкой подсветкой проблемных зон
        scatter = p.scatter('x', 'y', source=source, color='color', size=5, legend_label='Зона', alpha=0.6)

        # Добавление фона для аномалий
        for (start_idx, end_idx, anomaly_param, influence_level) in anomaly_intervals:
            if anomaly_param == param:
                if influence_level == 2:
                    color = 'red'
                    alpha = 0.2
                else:
                    color = 'orange'
                    alpha = 0.2
                box = BoxAnnotation(left=data_df.loc[start_idx, 'ds'], right=data_df.loc[end_idx, 'ds'],
                                    fill_color=color, fill_alpha=alpha)
                p.add_layout(box)

        # Добавление подсказок при наведении
        hover = HoverTool(
            tooltips=[
                ("Время", "@time{%F %T}"),
                (russian_labels[param], "@y{0.00}"),
                ("Зона", "@color")
            ],
            formatters={
                '@time': 'datetime',
            },
            mode='mouse',
            renderers=[scatter]  # Связывание HoverTool с конкретным глифом
        )
        p.add_tools(hover)

        # Настройка легенды
        p.legend.location = "top_left"
        p.legend.click_policy = "hide"

        plots.append(p)
    show(column(*plots))

# Метрика адекватности генерации данных
def evaluate_data(data_df, parameter_specs):
    adequacy_scores = {}
    for param in parameter_specs:
        # Оценка по нормальным данным (label == 0)
        data = data_df[param][data_df['label'] == 0]
        if len(data) == 0:
            adequacy_scores[param] = 0  # Если нет нормальных данных, установить 0
            continue
        mean_generated = np.mean(data)
        std_generated = np.std(data)
        mean_expected = parameter_specs[param]["mean"]
        std_expected = parameter_specs[param]["std"]

        # Чтобы избежать деления на ноль
        score_mean = 1 - min(abs(mean_generated - mean_expected) / (std_expected if std_expected != 0 else 1), 1)
        score_std = 1 - min(abs(std_generated - std_expected) / (std_expected if std_expected != 0 else 1), 1)
        adequacy_scores[param] = (score_mean + score_std) / 2  # Среднее между оценкой по среднему и СКО

    avg_score = np.mean(list(adequacy_scores.values()))
    print(f"Средняя метрика адекватности генерации данных: {avg_score:.2f}")
    for param, score in adequacy_scores.items():
        print(f"{param}: {score:.2f}")

# Пояснения к параметрам на русском языке
parameter_explanations = {
    "vibration_axis": "вибрация по одной из осей насоса. Повышенная вибрация может указывать на износ подшипников или несбалансированность.",
    "active_power": "активная мощность, потребляемая насосом. Увеличение может свидетельствовать о повышенной нагрузке или неэффективной работе.",
    "current_frequency": "частота тока насоса. Отклонения могут указывать на проблемы с электропитанием или двигателем.",
    "control_station_power": "мощность контрольной станции. Важный параметр для управления насосом и его работой.",
    "operating_current": "рабочий ток насоса. Повышение может сигнализировать о перегрузке или коротком замыкании.",
    "motor_temperature": "температура двигателя насоса. Повышение температуры может указывать на перегрев или недостаточное охлаждение.",
    "motor_load": "нагрузка на двигатель насоса. Высокая нагрузка может приводить к износу и перегреву.",
    "input_pressure": "давление на входе насоса. Снижение давления может свидетельствовать о засоре или утечке.",
    "output_pressure": "давление на выходе насоса. Повышение давления может указывать на засор или ограничение потока.",
    "flow_rate": "расход жидкости через насос. Снижение расхода может указывать на засор или утечку.",
    "resistance": "сопротивление насоса. Изменения сопротивления могут свидетельствовать о проблемах с уплотнениями или шлангами.",
    "bearing_temperature": "температура подшипников. Повышение температуры может указывать на износ или недостаточное смазывание.",
    "shaft_speed": "скорость вращения вала насоса. Отклонения от нормы могут указывать на проблемы с приводом или балансировкой."
}

# Пример использования
number_of_parameters = 10  # Максимальное количество параметров
number_of_intervals = 5
if number_of_parameters > len(parameter_specs):
    number_of_parameters = len(parameter_specs)
    print(f"Установлено количество параметров на максимум доступных: {number_of_parameters}")

chosen_parameters = random.sample(list(parameter_specs.keys()), number_of_parameters)
print("Выбранные параметры для введения трендов и аномалий:")
for param in chosen_parameters:
    print(f"- {param}: {parameter_explanations[param]}")

data_df, anomaly_intervals = generate_data(number_of_intervals, chosen_parameters, parameter_specs)
plot_parameters(data_df, anomaly_intervals)
evaluate_data(data_df, parameter_specs)

# Сохранение данных в CSV-файл
data_df.to_csv('pump_data.csv', index=False)
print("Данные сохранены в файл 'pump_data.csv'")

def export_to_excel_separate_sheets(data_df, filename="pump_data_separated.xlsx"):
    """
    Экспортирует данные в Excel, создавая отдельный лист для каждого параметра.
    Второй столбец каждого листа будет назван "1".
    
    :param data_df: DataFrame с синтетическими данными.
    :param filename: Имя Excel-файла для сохранения.
    """
    with pd.ExcelWriter(filename, engine='openpyxl') as writer:
        for column in data_df.columns:
            if column != "ds":  # Исключаем столбец с датами
                # Создание DataFrame с двумя колонками: "Дата" и "1"
                sheet_df = pd.DataFrame({
                    "Дата": data_df["ds"],
                    "1": data_df[column]  # Второй столбец всегда называется "1"
                })
                # Запись в отдельный лист
                sheet_df.to_excel(writer, sheet_name=column, index=False)
        print(f"Данные успешно экспортированы в {filename}")

# Пример вызова функции
export_to_excel_separate_sheets(data_df)

dd = pd.read_csv('/kaggle/working/pump_data.csv')
dd

Loading BokehJS ...

Выбранные параметры для введения трендов и аномалий:
- bearing_temperature: температура подшипников. Повышение температуры может указывать на износ или недостаточное смазывание.
- control_station_power: мощность контрольной станции. Важный параметр для управления насосом и его работой.
- output_pressure: давление на выходе насоса. Повышение давления может указывать на засор или ограничение потока.
- operating_current: рабочий ток насоса. Повышение может сигнализировать о перегрузке или коротком замыкании.
- vibration_axis: вибрация по одной из осей насоса. Повышенная вибрация может указывать на износ подшипников или несбалансированность.
- active_power: активная мощность, потребляемая насосом. Увеличение может свидетельствовать о повышенной нагрузке или неэффективной работе.
- flow_rate: расход жидкости через насос. Снижение расхода может указывать на засор или утечку.
- motor_load: нагрузка на двигатель насоса. Высокая нагрузка может приводить к износу и перегреву.
- current_frequency

Средняя метрика адекватности генерации данных: 0.60
vibration_axis: 0.96
active_power: 0.50
current_frequency: 0.96
control_station_power: 0.93
operating_current: 0.00
motor_temperature: 0.91
motor_load: 0.00
input_pressure: 0.00
output_pressure: 0.09
flow_rate: 0.93
resistance: 0.89
bearing_temperature: 0.87
shaft_speed: 0.76
Данные сохранены в файл 'pump_data.csv'
Данные успешно экспортированы в pump_data_separated.xlsx


ds  vibration_axis  active_power  current_frequency  \
0    2025-01-01 00:00:00        0.349579    109.923065          48.926768   
1    2025-01-01 01:00:00        0.412702    101.515789          49.777242   
2    2025-01-01 02:00:00        0.448807    101.981784          50.370020   
3    2025-01-01 03:00:00        0.330575    107.452326          51.045432   
4    2025-01-01 04:00:00        0.379440    104.326863          50.593612   
..                   ...             ...           ...                ...   
995  2025-02-11 11:00:00        0.600000     35.000000          40.000000   
996  2025-02-11 12:00:00        0.600000     35.000000          40.000000   
997  2025-02-11 13:00:00        0.600000     35.000000          40.000000   
998  2025-02-11 14:00:00        0.600000     35.000000          40.000000   
999  2025-02-11 15:00:00        0.600000     35.000000          40.000000   

     control_station_power  operating_current  motor_temperature  motor_load  \
0               111.023262               30.0          67.909200        90.0   
1                88.254786               30.0          56.187769        90.0   
2               100.338542               30.0          59.672945        90.0   
3               118.285240               30.0          62.164813        90.0   
4                89.544755               30.0          61.291656        90.0   
..                     ...                ...                ...         ...   
995              30.000000                5.0          20.000000        25.0   
996              30.000000                5.0          20.000000        25.0   
997              30.000000                5.0          20.000000        25.0   
998              30.000000                5.0          20.000000        25.0   
999              30.000000                5.0          20.000000        25.0   

     input_pressure  output_pressure  flow_rate  resistance  \
0              18.0        28.000000  42.045036   19.174493   
1              18.0        28.000000  51.771085   17.815946   
2              18.0        26.026477  54.881418   16.705636   
3              18.0        28.000000  48.067033   18.498538   
4              18.0        28.000000  47.934358   17.687748   
..              ...              ...        ...         ...   
995             2.5        10.000000  20.000000   24.000000   
996             2.5        10.000000  20.000000   24.000000   
997             2.5        10.000000  20.000000   24.000000   
998             2.5        10.000000  20.000000   24.000000   
999             2.5        10.000000  20.000000   24.000000   

     bearing_temperature  shaft_speed  label  
0              37.698715  1483.591741      0  
1              36.451798  1524.291221      0  
2              43.229869  1505.804317      0  
3              43.356495  1491.691876      0  
4              37.724079  1557.678223      0  
..                   ...          ...    ...  
995            25.000000  1200.000000      2  
996            25.000000  1200.000000      2  
997            25.000000  1200.000000      2  
998            25.000000  1200.000000      2  
999            25.000000  1200.000000      2  

[1000 rows x 15 columns]

In [19]:
# Для отображения графиков в Jupyter Notebook
output_notebook()

def generate_multiple_scenarios(number_of_scenarios, number_of_intervals, chosen_parameters, parameter_specs):
    """
    Генерирует несколько сценариев и объединяет их в единый временной ряд.

    :param number_of_scenarios: Количество сценариев для генерации.
    :param number_of_intervals: Количество интервалов для каждого сценария.
    :param chosen_parameters: Параметры для генерации аномалий.
    :param parameter_specs: Характеристики параметров.
    :return: Объединённый DataFrame с временными рядами.
    """
    combined_df = pd.DataFrame()
    current_start_time = pd.Timestamp("2025-01-01")  # Начальная дата

    for scenario_id in range(number_of_scenarios):
        # Генерация данных для сценария
        data_df, anomaly_intervals = generate_data(number_of_intervals, chosen_parameters, parameter_specs)

        # Сдвиг временных меток для текущего сценария
        data_df['ds'] = data_df['ds'] + (current_start_time - data_df['ds'].min())

        # Добавляем метку сценария для удобства
        data_df['scenario_id'] = scenario_id + 1

        # Обновляем время начала для следующего сценария
        current_start_time = data_df['ds'].max() + pd.Timedelta(hours=1)

        # Объединяем сценарии
        combined_df = pd.concat([combined_df, data_df], ignore_index=True)

    return combined_df

# Генерация 10 сценариев
number_of_scenarios = 10
combined_df = generate_multiple_scenarios(number_of_scenarios, number_of_intervals, chosen_parameters, parameter_specs)

# Сохранение объединённого датафрейма в CSV
combined_df.to_csv('/kaggle/working/combined_pump_data.csv', index=False)
print("Данные сохранены в файл 'combined_pump_data.csv'")

# Функция визуализации для нескольких сценариев
def plot_multiple_scenarios(combined_df):
    params = list(parameter_specs.keys())
    plots = []
    labels = {
        "vibration_axis": "Вибрация по оси",
        "active_power": "Активная мощность",
        "current_frequency": "Частота тока",
        "control_station_power": "Мощность контрольной станции",
        "operating_current": "Рабочий ток",
        "motor_temperature": "Температура двигателя",
        "motor_load": "Нагрузка на двигатель",
        "input_pressure": "Давление на входе",
        "output_pressure": "Давление на выходе",
        "flow_rate": "Расход жидкости",
        "resistance": "Сопротивление",
        "bearing_temperature": "Температура подшипников",
        "shaft_speed": "Скорость вращения вала"
    }

    for param in params:
        y_min = combined_df[param].min() * 0.9
        y_max = combined_df[param].max() * 1.1

        p = figure(title=f"{labels[param]} (по сценариям)", 
                   width=900, height=300, x_axis_label='Время', y_axis_label=param,
                   tools="pan,wheel_zoom,box_zoom,reset,save", y_range=(y_min, y_max), x_axis_type='datetime')

        # Закрашивание зон значений
        normal_low = parameter_specs[param]["normal_low"]
        normal_high = parameter_specs[param]["normal_high"]
        crit_low = parameter_specs[param]["crit_low"]
        crit_high = parameter_specs[param]["crit_high"]

        green_box = BoxAnnotation(top=normal_high, bottom=normal_low, fill_color='green', fill_alpha=0.1)
        yellow_box_top = BoxAnnotation(top=crit_high, bottom=normal_high, fill_color='yellow', fill_alpha=0.1)
        yellow_box_bottom = BoxAnnotation(top=normal_low, bottom=crit_low, fill_color='yellow', fill_alpha=0.1)
        red_box_top = BoxAnnotation(top=y_max, bottom=crit_high, fill_color='red', fill_alpha=0.1)
        red_box_bottom = BoxAnnotation(top=crit_low, bottom=y_min, fill_color='red', fill_alpha=0.1)

        p.add_layout(green_box)
        p.add_layout(yellow_box_top)
        p.add_layout(yellow_box_bottom)
        p.add_layout(red_box_top)
        p.add_layout(red_box_bottom)

        # Добавление данных для каждого сценария
        for scenario_id in sorted(combined_df['scenario_id'].unique()):
            scenario_data = combined_df[combined_df['scenario_id'] == scenario_id]
            source = ColumnDataSource(data=dict(
                x=scenario_data['ds'],
                y=scenario_data[param],
                label=scenario_data['label'],
                time=scenario_data['ds']
            ))

            # Линия для текущего сценария
            p.line('x', 'y', source=source, alpha=0.7, legend_label=f"Сценарий {scenario_id}")

            # Точки окрашиваются по зоне
            colors = []
            for value in scenario_data[param]:
                if normal_low <= value <= normal_high:
                    colors.append('green')  # Нормальная зона
                elif (crit_low <= value < normal_low) or (normal_high < value <= crit_high):
                    colors.append('yellow')  # Предкритическая зона
                else:
                    colors.append('red')  # Критическая зона
            source.data['color'] = colors

            # Точки
            p.scatter('x', 'y', source=source, color='color', size=5, alpha=0.6)

        # Вертикальные линии для разделения сценариев
        for start_time in combined_df.groupby('scenario_id')['ds'].min():
            p.add_layout(BoxAnnotation(left=start_time, right=start_time + pd.Timedelta(minutes=1), 
                                       line_color="black", line_width=2, line_alpha=0.8))

        # Подсказки при наведении
        hover = HoverTool(
            tooltips=[
                ("Время", "@time{%F %T}"),
                (labels[param], "@y{0.00}"),
                ("Зона", "@color")
            ],
            formatters={
                '@time': 'datetime',
            },
            mode='mouse'
        )
        p.add_tools(hover)

        p.legend.location = "top_left"
        p.legend.click_policy = "hide"

        plots.append(p)

    # Отображение всех графиков
    show(column(*plots))

# Вызов функции для визуализации
plot_multiple_scenarios(combined_df)

dd = pd.read_csv('/kaggle/working/combined_pump_data.csv')
dd

def export_to_excel_separate_sheets(data_df, filename="combined_pump_data_separated.xlsx"):
    """
    Экспортирует данные в Excel, создавая отдельный лист для каждого параметра.
    Второй столбец каждого листа будет назван "1".
    
    :param data_df: DataFrame с синтетическими данными.
    :param filename: Имя Excel-файла для сохранения.
    """
    with pd.ExcelWriter(filename, engine='openpyxl') as writer:
        for column in data_df.columns:
            if column != "ds":  # Исключаем столбец с датами
                # Создание DataFrame с двумя колонками: "Дата" и "1"
                sheet_df = pd.DataFrame({
                    "Дата": data_df["ds"],
                    "1": data_df[column]  # Второй столбец всегда называется "1"
                })
                # Запись в отдельный лист
                sheet_df.to_excel(writer, sheet_name=column, index=False)
        print(f"Данные успешно экспортированы в {filename}")

# Пример вызова функции
export_to_excel_separate_sheets(combined_df)

Loading BokehJS ...

Данные сохранены в файл 'combined_pump_data.csv'


Данные успешно экспортированы в combined_pump_data_separated.xlsx
